In [1]:
from bokeh.plotting import figure, show
from bokeh.layouts import column
from bokeh.io import output_notebook
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import neo

output_notebook()

Loading BokehJS ...

In [2]:
import os
os.listdir('Sample data')

['10Hz_1V_neg500mV_1ms003.ns5',
 '10Hz_1V_neg500mV_1ms_TTX007.ns5',
 'NO_STIM_NO_GEN002.ns5',
 '6_Eyes_data.mat']

# Read data

In [3]:
def get_signal(filepath='Sample data/10Hz_1V_neg500mV_1ms003.ns5', verbose=1):
    reader = neo.io.BlackrockIO(filename=filepath)
    print("No. blocks", reader.block_count())
    block = reader.read_block()
    print("Block size", block.size)
    segment = block.segments[0]
    print("Segment size", segment.size)
    signal = segment.analogsignals[0]
    print("Signal shape (timestampts, signals)", signal.shape)
    time = np.array(signal.times)
    print(f"Time duration {time[-1]}s")
    return time, signal.magnitude

time, stimulated = get_signal('Sample data/10Hz_1V_neg500mV_1ms003.ns5')
time, ttx = get_signal('Sample data/10Hz_1V_neg500mV_1ms_TTX007.ns5')



No. blocks 1
Block size {'segments': 1, 'groups': 1}
Segment size {'analogsignals': 1, 'epochs': 0, 'events': 0, 'irregularlysampledsignals': 0, 'spiketrains': 0, 'imagesequences': 0}
Signal shape (timestampts, signals) (300300, 32)
Time duration 10.009966666666667s
No. blocks 1
Block size {'segments': 1, 'groups': 1}
Segment size {'analogsignals': 1, 'epochs': 0, 'events': 0, 'irregularlysampledsignals': 0, 'spiketrains': 0, 'imagesequences': 0}
Signal shape (timestampts, signals) (300300, 32)
Time duration 10.009966666666667s


In [4]:
channel_no = 1

In [5]:
# the perfect ttx signal
# we have 30KHz sampling rate and 1 ms (0.001 s) stimulation, then 1 stimulation is 30 samples
p = figure(title="Signal", x_axis_label='time (s)', y_axis_label='Voltage (V)', width=1200, height=400)
initial_offset = 1910 #eyeballing
offset = 3000 #known
sa_length = 200 #eyeballing
for i in range(3):
    p.line(time[initial_offset+i*offset:initial_offset+sa_length+i*offset], 
           ttx[:, channel_no][initial_offset+i*offset:initial_offset+sa_length+i*offset], 
           color='orange', width=2)
show(p)

In [6]:
# collect all stimulation artefacts from ttx and average them
sa = []
no_sa = 100
for i in range(no_sa):
    sa.append(ttx[:, 0][initial_offset+i*offset:initial_offset+sa_length+i*offset])

sa = np.array(sa)
stimulation_artifact_ttx = sa.mean(axis=0)

# plot the average stimulation artefact
p = figure(title="Averaged TTX stimulation artefact", x_axis_label='time (s)', y_axis_label='Voltage (V)', width=1200, height=400)
p.line(time[0:len(stimulation_artifact_ttx)], stimulation_artifact_ttx, color='orange', width=2)
show(p)

In [7]:
# find initial offset for stimulated signal /eyeballing

p = figure(title="Signal", x_axis_label='time (s)', y_axis_label='Voltage (V)', width=1200, height=400)
initial_offset = 894 #eyeballing
p.line(time[:50000], stimulated[:, 0][:50000], legend_label="Channel 1", line_width=2, alpha=0.5)
for i in range(17):
    p.line(time[initial_offset+i*offset:initial_offset+sa_length+i*offset],
           stimulation_artifact_ttx, color='orange', width=2)

show(p)

# subtract stimulation artefact from stimulated signal

channel_clean = stimulated[:, channel_no].copy()
for i in range(100):
    channel_clean[initial_offset+i*offset:initial_offset+sa_length+i*offset] -= stimulation_artifact_ttx

p2 = figure(title="Substracted signal", x_axis_label='time (s)', y_axis_label='Voltage (V)', width=1200, height=400, x_range=p.x_range)
p2.line(time[:50000], channel_clean[:50000], legend_label="Channel 1", line_width=2, alpha=0.5)
show(column(p, p2))

# this doesn't seem to work, let's try to create "the perfect stimulation artefact" using the actual stimulation signal

In [11]:
# collect all stimulation artefacts from stimulation and average them
sa = []
no_sa = 100
for i in range(no_sa):
    sa.append(stimulated[:, 0][initial_offset+i*offset:initial_offset+sa_length+i*offset])

sa = np.array(sa)
stimulation_artifact = sa.mean(axis=0)

# plot the average stimulation artefact
p = figure(title="Averaged STIMULATED stimulation artefact", x_axis_label='time (s)', y_axis_label='Voltage (V)', width=1200, height=400)
p.line(time[0:len(stimulation_artifact)], stimulation_artifact, color='orange', width=2)
show(p)

In [12]:


# find initial offset for stimulated signal /eyeballing


p = figure(title="Signal", x_axis_label='time (s)', y_axis_label='Voltage (V)', width=1200, height=400)
p.line(time[:50000], stimulated[:, 0][:50000], legend_label="Channel 1", line_width=2, alpha=0.5)
for i in range(17):
    p.line(time[initial_offset+i*offset:initial_offset+sa_length+i*offset],
           stimulation_artifact, color='orange', width=2)

# subtract stimulation artefact from stimulated signal

channel_clean = stimulated[:, channel_no].copy()
for i in range(100):
    channel_clean[initial_offset+i*offset:initial_offset+sa_length+i*offset] -= stimulation_artifact

p2 = figure(title="Subtracted signal", x_axis_label='time (s)', y_axis_label='Voltage (V)', width=1200, height=400, x_range=p.x_range)
p2.line(time[:50000], channel_clean[:50000], legend_label="Channel 1", line_width=2, alpha=0.5)
show(column(p, p2))